Parsing semantyczny z wykorzystaniem technik uczenia maszynowego
================================================================

Wprowadzenie
------------
Problem wykrywania slotów i ich wartości w wypowiedziach użytkownika można sformułować jako zadanie
polegające na przewidywaniu dla poszczególnych słów etykiet wskazujących na to czy i do jakiego
slotu dane słowo należy.

<pre>chciałbym zarezerwować stolik na jutro<b>/day</b> na godzinę dwunastą<b>/hour</b> czterdzieści<b>/hour</b> pięć<b>/hour</b> na pięć<b>/size</b> osób</pre>

Granice slotów oznacza się korzystając z wybranego schematu etykietowania.

### Schemat IOB

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |

<pre>chciałbym zarezerwować stolik na jutro<b>/B-day</b> na godzinę dwunastą<b>/B-hour</b> czterdzieści<b>/I-hour</b> pięć<b>/I-hour</b> na pięć<b>/B-size</b> osób</pre>

### Schemat IOBES

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |
| E      | koniec slotu (ending)      |
| S      | pojedyncze słowo (single)  |

<pre>chciałbym zarezerwować stolik na jutro<b>/S-day</b> na godzinę dwunastą<b>/B-hour</b> czterdzieści<b>/I-hour</b> pięć<b>/E-hour</b> na pięć<b>/S-size</b> osób</pre>

Jeżeli dla tak sformułowanego zadania przygotujemy zbiór danych
złożony z wypowiedzi użytkownika z oznaczonymi slotami (tzw. *zbiór uczący*),
to możemy zastosować techniki (nadzorowanego) uczenia maszynowego w celu zbudowania modelu
annotującego wypowiedzi użytkownika etykietami slotów.

Do zbudowania takiego modelu można wykorzystać między innymi:

 1. warunkowe pola losowe (Lafferty i in.; 2001),

 2. rekurencyjne sieci neuronowe, np. sieci LSTM (Hochreiter i Schmidhuber; 1997),

 3. transformery (Vaswani i in., 2017).

Przykład
--------
Skorzystamy ze zbioru danych przygotowanego przez Schustera (2019).

In [1]:
!mkdir -p l07
%cd l07
!curl -L -C -  https://fb.me/multilingual_task_oriented_data  -o data.zip
!unzip data.zip
%cd ..

g:\studia\studia uam\systemy dialogowe\notebooks\l07


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
 14 8714k   14 1307k    0     0   860k      0  0:00:10  0:00:01  0:00:09 1354k
100 8714k  100 8714k    0     0  4650k      0  0:00:01  0:00:01 --:--:-- 6606k


g:\studia\studia uam\systemy dialogowe\notebooks


'unzip' is not recognized as an internal or external command,
operable program or batch file.


'Expand-Archive' is not recognized as an internal or external command,
operable program or batch file.


Zbiór ten gromadzi wypowiedzi w trzech językach opisane slotami dla dwunastu ram należących do trzech dziedzin `Alarm`, `Reminder` oraz `Weather`. Dane wczytamy korzystając z biblioteki [conllu](https://pypi.org/project/conllu/).

In [6]:
from conllu import parse_incr
fields = ['id', 'form', 'frame', 'slot']

def nolabel2o(line, i):
    return 'O' if line[i] == 'NoLabel' else line[i]

with open('l07/en/train-en.conllu') as trainfile:
    trainset = list(parse_incr(trainfile, fields=fields, field_parsers={'slot': nolabel2o}))
with open('l07/en/test-en.conllu') as testfile:
    testset = list(parse_incr(testfile, fields=fields, field_parsers={'slot': nolabel2o}))

Zobaczmy kilka przykładowych wypowiedzi z tego zbioru.

In [7]:
from tabulate import tabulate
tabulate(trainset[0], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>tell   </td><td>weather/find</td><td>O             </td></tr>\n<tr><td style="text-align: right;">2</td><td>me     </td><td>weather/find</td><td>O             </td></tr>\n<tr><td style="text-align: right;">3</td><td>the    </td><td>weather/find</td><td>O             </td></tr>\n<tr><td style="text-align: right;">4</td><td>weather</td><td>weather/find</td><td>B-weather/noun</td></tr>\n<tr><td style="text-align: right;">5</td><td>report </td><td>weather/find</td><td>I-weather/noun</td></tr>\n<tr><td style="text-align: right;">6</td><td>for    </td><td>weather/find</td><td>O             </td></tr>\n<tr><td style="text-align: right;">7</td><td>half   </td><td>weather/find</td><td>B-location    </td></tr>\n<tr><td style="text-align: right;">8</td><td>moon   </td><td>weather/find</td><td>I-location    </td></tr>\n<tr><td style="text-align: right;">9</td><td>bay    </td><td>weather/find</td><td>I-location    </td></tr>\n</tbody>\n</table>'

In [8]:
tabulate(trainset[1000], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>remind</td><td>reminder/set_reminder</td><td>O              </td></tr>\n<tr><td style="text-align: right;">2</td><td>me    </td><td>reminder/set_reminder</td><td>O              </td></tr>\n<tr><td style="text-align: right;">3</td><td>about </td><td>reminder/set_reminder</td><td>O              </td></tr>\n<tr><td style="text-align: right;">4</td><td>game  </td><td>reminder/set_reminder</td><td>B-reminder/todo</td></tr>\n<tr><td style="text-align: right;">5</td><td>night </td><td>reminder/set_reminder</td><td>I-reminder/todo</td></tr>\n<tr><td style="text-align: right;">6</td><td>on    </td><td>reminder/set_reminder</td><td>B-datetime     </td></tr>\n<tr><td style="text-align: right;">7</td><td>friday</td><td>reminder/set_reminder</td><td>I-datetime     </td></tr>\n<tr><td style="text-align: right;">8</td><td>at    </td><td>reminder/set_reminder</td><td>I-datetime     </td></tr>\n<tr><td style="text-align: right;">9</td><td>4pm   </td><td>reminder/set_reminder</td><td>I-datetime     </td></tr>\n</tbody>\n</table>'

In [9]:
tabulate(trainset[2000], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>set    </td><td>alarm/set_alarm</td><td>O         </td></tr>\n<tr><td style="text-align: right;">2</td><td>alarm  </td><td>alarm/set_alarm</td><td>O         </td></tr>\n<tr><td style="text-align: right;">3</td><td>for    </td><td>alarm/set_alarm</td><td>B-datetime</td></tr>\n<tr><td style="text-align: right;">4</td><td>20     </td><td>alarm/set_alarm</td><td>I-datetime</td></tr>\n<tr><td style="text-align: right;">5</td><td>minutes</td><td>alarm/set_alarm</td><td>I-datetime</td></tr>\n</tbody>\n</table>'

Na potrzeby prezentacji procesu uczenia w jupyterowym notatniku zawęzimy zbiór danych do początkowych przykładów.

In [10]:
trainset = trainset[:300]
testset = testset[:300]

Budując model skorzystamy z architektury opartej o rekurencyjne sieci neuronowe
zaimplementowanej w bibliotece [flair](https://github.com/flairNLP/flair) (Akbik i in. 2018).

In [13]:
from flair.data import Corpus, Sentence, Token
from flair.datasets import FlairDatapointDataset
from flair.embeddings import StackedEmbeddings
from flair.embeddings import WordEmbeddings
from flair.embeddings import CharacterEmbeddings
from flair.embeddings import FlairEmbeddings
from flair.models import SequenceTagger
from flair.trainers import ModelTrainer

# determinizacja obliczeń
import random
import torch
random.seed(42)
torch.manual_seed(42)

if torch.cuda.is_available():
    torch.cuda.manual_seed(0)
    torch.cuda.manual_seed_all(0)
    torch.backends.cudnn.enabled = False
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

c:\Users\macty\AppData\Local\Programs\Python\Python311\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Dane skonwertujemy do formatu wykorzystywanego przez `flair`, korzystając z następującej funkcji.

In [14]:
def conllu2flair(sentences, label=None):
    fsentences = []

    for sentence in sentences:
        fsentence = Sentence(' '.join(token['form'] for token in sentence), use_tokenizer=False)
        start_idx = None
        end_idx = None
        tag = None

        if label:
            for idx, (token, ftoken) in enumerate(zip(sentence, fsentence)):
                if token[label].startswith('B-'):
                    start_idx = idx
                    end_idx = idx
                    tag = token[label][2:]
                elif token[label].startswith('I-'):
                    end_idx = idx
                elif token[label] == 'O':
                    if start_idx is not None:
                        fsentence[start_idx:end_idx+1].add_label(label, tag)
                        start_idx = None
                        end_idx = None
                        tag = None

            if start_idx is not None:
                fsentence[start_idx:end_idx+1].add_label(label, tag)

        fsentences.append(fsentence)

    return FlairDatapointDataset(fsentences)

corpus = Corpus(train=conllu2flair(trainset, 'slot'), test=conllu2flair(testset, 'slot'))
print(corpus)
tag_dictionary = corpus.make_label_dictionary(label_type='slot')
print(tag_dictionary)

Corpus: 270 train + 30 dev + 300 test sentences
2023-04-16 23:32:52,141 Computing label dictionary. Progress:


270it [00:00, 53998.76it/s]

2023-04-16 23:32:52,151 Dictionary created for label 'slot' with 5 values: datetime (seen 174 times), weather/attribute (seen 77 times), weather/noun (seen 66 times), location (seen 44 times)
Dictionary with 5 tags: <unk>, datetime, weather/attribute, weather/noun, location


Nasz model będzie wykorzystywał wektorowe reprezentacje słów (zob. [Word Embeddings](https://github.com/flairNLP/flair/blob/master/resources/docs/TUTORIAL_EMBEDDINGS_OVERVIEW.md)).

In [15]:
embedding_types = [
    WordEmbeddings('en'),
    FlairEmbeddings('en-forward'),
    FlairEmbeddings('en-backward'),
    CharacterEmbeddings(),
]

embeddings = StackedEmbeddings(embeddings=embedding_types)
tagger = SequenceTagger(hidden_size=256, embeddings=embeddings,
                        tag_dictionary=tag_dictionary,
                        tag_type='slot', use_crf=True)

2023-04-16 23:32:52,457 https://flair.informatik.hu-berlin.de/resources/embeddings/token/en-fasttext-news-300d-1M.vectors.npy not found in cache, downloading to C:\Users\macty\AppData\Local\Temp\tmpxx1l309v


100%|██████████| 1.12G/1.12G [01:03<00:00, 18.8MB/s]

2023-04-16 23:33:56,277 copying C:\Users\macty\AppData\Local\Temp\tmpxx1l309v to cache at C:\Users\macty\.flair\embeddings\en-fasttext-news-300d-1M.vectors.npy


2023-04-16 23:33:57,359 removing temp file C:\Users\macty\AppData\Local\Temp\tmpxx1l309v
2023-04-16 23:33:58,068 https://flair.informatik.hu-berlin.de/resources/embeddings/token/en-fasttext-news-300d-1M not found in cache, downloading to C:\Users\macty\AppData\Local\Temp\tmpnqnow7h9


100%|██████████| 52.1M/52.1M [00:02<00:00, 18.9MB/s]

...

100%|██████████| 69.7M/69.7M [00:03<00:00, 22.5MB/s]

2023-04-16 23:34:17,584 copying C:\Users\macty\AppData\Local\Temp\tmp1i_pq3dr to cache at C:\Users\macty\.flair\embeddings\news-backward-0.4.1.pt
2023-04-16 23:34:17,631 removing temp file C:\Users\macty\AppData\Local\Temp\tmp1i_pq3dr


2023-04-16 23:34:18,016 https://flair.informatik.hu-berlin.de/resources/characters/common_characters not found in cache, downloading to C:\Users\macty\AppData\Local\Temp\tmpqyh0003q


100%|██████████| 2.82k/2.82k [00:00<00:00, 1.44MB/s]

2023-04-16 23:34:18,139 copying C:\Users\macty\AppData\Local\Temp\tmpqyh0003q to cache at C:\Users\macty\.flair\datasets\common_characters
2023-04-16 23:34:18,145 removing temp file C:\Users\macty\AppData\Local\Temp\tmpqyh0003q
2023-04-16 23:34:18,147 SequenceTagger predicts: Dictionary with 17 tags: O, S-datetime, B-datetime, E-datetime, I-datetime, S-weather/attribute, B-weather/attribute, E-weather/attribute, I-weather/attribute, S-weather/noun, B-weather/noun, E-weather/noun, I-weather/noun, S-location, B-location, E-location, I-location


Zobaczmy jak wygląda architektura sieci neuronowej, która będzie odpowiedzialna za przewidywanie
slotów w wypowiedziach.

In [16]:
print(tagger)

SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings(
      'en'
      (embedding): Embedding(1000001, 300)
    )
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.05, inplace=False)
        (encoder): Embedding(300, 100)
        (rnn): LSTM(100, 2048)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.05, inplace=False)
        (encoder): Embedding(300, 100)
        (rnn): LSTM(100, 2048)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dropout): LockedDropout(p=0.5)
  (embedding2nn): Linear(in_features=4446, out_features=4446, bias=True)
  (rnn): LSTM(4446, 256, batch_first=True, bidirectional=True)
  (linear): Linear(in_features=512, out_features=19, bias=True)
  (loss_function): Vite

Wykonamy dziesięć iteracji (epok) uczenia a wynikowy model zapiszemy w katalogu `slot-model`.

In [17]:
trainer = ModelTrainer(tagger, corpus)
trainer.train('slot-model',
              learning_rate=0.1,
              mini_batch_size=32,
              max_epochs=10,
              train_with_dev=False)

2023-04-16 23:34:18,357 ----------------------------------------------------------------------------------------------------
2023-04-16 23:34:18,358 Model: "SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings(
      'en'
      (embedding): Embedding(1000001, 300)
    )
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.05, inplace=False)
        (encoder): Embedding(300, 100)
        (rnn): LSTM(100, 2048)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.05, inplace=False)
        (encoder): Embedding(300, 100)
        (rnn): LSTM(100, 2048)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dropout): LockedDropout(p=0.5)
  (embedding2nn): Linear(in_features=4446, out_features=4446, bias

100%|██████████| 1/1 [00:01<00:00,  1.12s/it]

2023-04-16 23:34:29,797 Evaluating as a multi-label problem: False
2023-04-16 23:34:29,806 DEV : loss 1.2717913389205933 - f1-score (micro avg)  0.0357
2023-04-16 23:34:29,808 BAD EPOCHS (no improvement): 0
2023-04-16 23:34:29,809 saving best model


2023-04-16 23:34:41,288 ----------------------------------------------------------------------------------------------------
2023-04-16 23:34:42,050 epoch 2 - iter 1/9 - loss 1.43326204 - time (sec): 0.76 - samples/sec: 241.47 - lr: 0.100000
2023-04-16 23:34:42,846 epoch 2 - iter 2/9 - loss 1.40312603 - time (sec): 1.56 - samples/sec: 234.92 - lr: 0.100000
2023-04-16 23:34:43,571 epoch 2 - iter 3/9 - loss 1.39219711 - time (sec): 2.28 - samples/sec: 235.65 - lr: 0.100000
2023-04-16 23:34:44,338 epoch 2 - iter 4/9 - loss 1.38006975 - time (sec): 3.05 - samples/sec: 232.13 - lr: 0.100000
2023-04-16 23:34:45,066 epoch 2 - iter 5/9 - loss 1.34341906 - time (sec): 3.78 - samples/sec: 232.93 - lr: 0.100000
2023-04-16 23:34:45,850 epoch 2 - iter 6/9 - loss 1.31603716 - time (sec): 4.56 - samples/sec: 234.55 - lr: 0.100000
2023-04-16 23:34:46,612 epoch 2 - iter 7/9 - loss 1.28879818 - time (sec): 5.32 - samples/sec: 237.23 - lr: 0.100000
2023-04-16 23:34:47,400 epoch 2 - iter 8/9 - loss 1.2735

100%|██████████| 1/1 [00:00<00:00,  4.76it/s]

...

2023-04-16 23:36:20,082 Evaluating as a multi-label problem: False
2023-04-16 23:36:20,089 DEV : loss 0.03223632648587227 - f1-score (micro avg)  0.9275
2023-04-16 23:36:20,091 BAD EPOCHS (no improvement): 2


2023-04-16 23:36:31,813 ----------------------------------------------------------------------------------------------------
2023-04-16 23:36:35,403 SequenceTagger predicts: Dictionary with 19 tags: O, S-datetime, B-datetime, E-datetime, I-datetime, S-weather/attribute, B-weather/attribute, E-weather/attribute, I-weather/attribute, S-weather/noun, B-weather/noun, E-weather/noun, I-weather/noun, S-location, B-location, E-location, I-location, <START>, <STOP>


100%|██████████| 10/10 [00:13<00:00,  1.40s/it]

2023-04-16 23:36:50,601 Evaluating as a multi-label problem: False
2023-04-16 23:36:50,612 0.2111	0.1989	0.2048	0.1176
2023-04-16 23:36:50,613 
Results:
- F-score (micro) 0.2048
- F-score (macro) 0.1106
- Accuracy 0.1176

By class:
                           precision    recall  f1-score   support

                 datetime     0.2136    0.2327    0.2227       202
             weather/noun     0.2184    0.5588    0.3140        34
            reminder/todo     0.0000    0.0000    0.0000        46
            reminder/noun     0.0000    0.0000    0.0000        42
        weather/attribute     0.1765    0.1667    0.1714        18
                 location     0.1765    0.1765    0.1765        17
reminder/recurring_period     0.0000    0.0000    0.0000         2
                 negation     0.0000    0.0000    0.0000         1

                micro avg     0.2111    0.1989    0.2048       362
                macro avg     0.0981    0.1418    0.1106       362
             weighted avg    

{'test_score': 0.20483641536273117,
 'dev_score_history': [0.03571428571428571,
  0.0,
  0.7761194029850745,
  0.923076923076923,
  0.9705882352941176,
  0.9705882352941176,
  0.9705882352941176,
  0.9705882352941176,
  0.9705882352941176,
  0.9275362318840579],
 'train_loss_history': [2.279269006857918,
  1.2743978126256028,
  0.7800527689157958,
  0.40072541558857516,
  0.22090499240102493,
  0.14176936011605706,
  0.09412068554059486,
  0.08690436752662781,
  0.08649074149668408,
  0.06249183581189711],
 'dev_loss_history': [1.2717913389205933,
  0.7916695475578308,
  0.33898717164993286,
  0.16208426654338837,
  0.07899065315723419,
  0.05525948479771614,
  0.04532366245985031,
  0.024222934618592262,
  0.0387137271463871,
  0.03223632648587227]}

Jakość wyuczonego modelu możemy ocenić, korzystając z zaraportowanych powyżej metryk, tj.:

 - *tp (true positives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fp (false positives)*

   > liczba słów nieoznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fn (false negatives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, którym model nie nadał etykiety $e$

 - *precision*

   > $$\frac{tp}{tp + fp}$$

 - *recall*

   > $$\frac{tp}{tp + fn}$$

 - $F_1$

   > $$\frac{2 \cdot precision \cdot recall}{precision + recall}$$

 - *micro* $F_1$

   > $F_1$ w którym $tp$, $fp$ i $fn$ są liczone łącznie dla wszystkich etykiet, tj. $tp = \sum_{e}{{tp}_e}$, $fn = \sum_{e}{{fn}_e}$, $fp = \sum_{e}{{fp}_e}$

 - *macro* $F_1$

   > średnia arytmetyczna z $F_1$ obliczonych dla poszczególnych etykiet z osobna.

Wyuczony model możemy wczytać z pliku korzystając z metody `load`.

In [18]:
model = SequenceTagger.load('slot-model/final-model.pt')

2023-04-16 23:37:00,272 SequenceTagger predicts: Dictionary with 19 tags: O, S-datetime, B-datetime, E-datetime, I-datetime, S-weather/attribute, B-weather/attribute, E-weather/attribute, I-weather/attribute, S-weather/noun, B-weather/noun, E-weather/noun, I-weather/noun, S-location, B-location, E-location, I-location, <START>, <STOP>


Wczytany model możemy wykorzystać do przewidywania slotów w wypowiedziach użytkownika, korzystając
z przedstawionej poniżej funkcji `predict`.

In [19]:
def predict(model, sentence):
    csentence = [{'form': word, 'slot': 'O'} for word in sentence]
    fsentence = conllu2flair([csentence])[0]
    model.predict(fsentence)

    for span in fsentence.get_spans('slot'):
        tag =  span.get_label('slot').value
        csentence[span.tokens[0].idx - 1]['slot'] = f'B-{tag}'

        for token in span.tokens[1:]:
            csentence[token.idx - 1]['slot'] = f'I-{tag}'

    return csentence


In [20]:
tabulate(predict(model, 'set alarm for 20 minutes'.split()), tablefmt='html')

'<table>\n<tbody>\n<tr><td>set    </td><td>O         </td></tr>\n<tr><td>alarm  </td><td>O         </td></tr>\n<tr><td>for    </td><td>B-datetime</td></tr>\n<tr><td>20     </td><td>B-datetime</td></tr>\n<tr><td>minutes</td><td>I-datetime</td></tr>\n</tbody>\n</table>'

In [21]:
tabulate(predict(model, 'change my 3 pm alarm to the next day'.split()), tablefmt='html')

'<table>\n<tbody>\n<tr><td>change</td><td>O             </td></tr>\n<tr><td>my    </td><td>O             </td></tr>\n<tr><td>3     </td><td>O             </td></tr>\n<tr><td>pm    </td><td>O             </td></tr>\n<tr><td>alarm </td><td>O             </td></tr>\n<tr><td>to    </td><td>O             </td></tr>\n<tr><td>the   </td><td>O             </td></tr>\n<tr><td>next  </td><td>O             </td></tr>\n<tr><td>day   </td><td>B-weather/noun</td></tr>\n</tbody>\n</table>'

Literatura
----------
 1. Sebastian Schuster, Sonal Gupta, Rushin Shah, Mike Lewis, Cross-lingual Transfer Learning for Multilingual Task Oriented Dialog. NAACL-HLT (1) 2019, pp. 3795-3805
 2. John D. Lafferty, Andrew McCallum, and Fernando C. N. Pereira. 2001. Conditional Random Fields: Probabilistic Models for Segmenting and Labeling Sequence Data. In Proceedings of the Eighteenth International Conference on Machine Learning (ICML '01). Morgan Kaufmann Publishers Inc., San Francisco, CA, USA, 282–289, https://repository.upenn.edu/cgi/viewcontent.cgi?article=1162&context=cis_papers
 3. Sepp Hochreiter and Jürgen Schmidhuber. 1997. Long Short-Term Memory. Neural Comput. 9, 8 (November 15, 1997), 1735–1780, https://doi.org/10.1162/neco.1997.9.8.1735
 4. Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N. Gomez, Lukasz Kaiser, Illia Polosukhin, Attention is All you Need, NIPS 2017, pp. 5998-6008, https://arxiv.org/abs/1706.03762
 5. Alan Akbik, Duncan Blythe, Roland Vollgraf, Contextual String Embeddings for Sequence Labeling, Proceedings of the 27th International Conference on Computational Linguistics, pp. 1638–1649, https://www.aclweb.org/anthology/C18-1139.pdf
